## Task 2 - Recommender System 


### Introduction 

Recommender systems are algorithms that uses data to help predict what a user might be interested from a variety of options based on the data gathered from the user's preference or data gathered from other users that like similar items. The feedback used to make these predictions are of two types: 

- **Explicit feedback:** Like the name suggests explicit feedback is a type of feedback that a user gives that is direct and precise like a rating or a like or a retweet. It's a type of feedback that is quantifiable. It provides a measurable yardstick of how much a user likes a particular item. This type of feedback is not abundant because users do not always give explicit feedback. 

- **Implicit feedback:** On the other hand, implicit feedback is a little more abundant but it attempts to measure a user's interaction strength. It's a little more vague and unclear. An example of this is a user playing a video, or the length of time a user spends watching a movie. 

There are different types of recommender systems, but the one of interest for this task is the collaborative filtering recommender system. 

Collaborative filtering algorithm predicts recommendations based on preference information from other users. Basically if you and another user have similar interest based on your implicit feedback, the recommender assumes that based on the similar interests between you and said user have, it can recommend another item that the users likes.  


This task is to build a recommender system for Steam, an online video game distribution service. The dataset provided contains details on the games different members have purchased and played, along with the number of hours they have played each game.
The dataset provided contains four columns:

• The first column contains a unique identifier for each member (user). 

• The second column contains the name of the game they purchased or played

• The third column contains details of the member behaviour, either ‘purchase’ or
‘play’. Because a game has to be purchased before it can be played there will be
two entries for the same game / member combination in some instances

• The fourth is set to 1 for rows where the behaviour is ‘purchase’. For rows where
the behaviours is ‘play’ the value in the fourth column corresponds to the number
of hours of play
We can use both purchase and play behaviours as implicit user feedback. 

A collaborative filtering recommender system will be built using the purchase and play behaviours from the dataset as implicit feedbacks. The Alternating Least Square ALS algorithm provided by Apache Spark's MLlib Library will be used to train the model and evaluate it's performance. 

In [0]:
# import mlflow and autolog machine learning runs 
import mlflow

mlflow.pyspark.ml.autolog()

### Data Import and Data Preprocessing 
The first step in the process is to upload the file to the Databricks Filesystem. Databricks provides a simple way via the Dashboard to do this. After this, I previewed the file using Databricks utility command dbutils.fs.head.

After previewing the file, I created a custom schema in the next cell for the csv file. This is so I could create clearer column names as I'm converting the CSV to a Dataframe. 

In [0]:

# This first three lines saves the file path to a variable. This is done so the variable is reusable across multiple cells without having to declare it every time. This embodies a programming paridgm called DRY. DRY means do not repeat yourself. 

file_directory = "/FileStore/tables"
file_name = "/steam_200k.csv"
file_path = file_directory + file_name

dbutils.fs.head(file_path)

[Truncated to first 65536 bytes]
Out[2]: '151603712,The Elder Scrolls V Skyrim,purchase,1\r\n151603712,The Elder Scrolls V Skyrim,play,273\r\n151603712,Fallout 4,purchase,1\r\n151603712,Fallout 4,play,87\r\n151603712,Spore,purchase,1\r\n151603712,Spore,play,14.9\r\n151603712,Fallout New Vegas,purchase,1\r\n151603712,Fallout New Vegas,play,12.1\r\n151603712,Left 4 Dead 2,purchase,1\r\n151603712,Left 4 Dead 2,play,8.9\r\n151603712,HuniePop,purchase,1\r\n151603712,HuniePop,play,8.5\r\n151603712,Path of Exile,purchase,1\r\n151603712,Path of Exile,play,8.1\r\n151603712,Poly Bridge,purchase,1\r\n151603712,Poly Bridge,play,7.5\r\n151603712,Left 4 Dead,purchase,1\r\n151603712,Left 4 Dead,play,3.3\r\n151603712,Team Fortress 2,purchase,1\r\n151603712,Team Fortress 2,play,2.8\r\n151603712,Tomb Raider,purchase,1\r\n151603712,Tomb Raider,play,2.5\r\n151603712,The Banner Saga,purchase,1\r\n151603712,The Banner Saga,play,2\r\n151603712,Dead Island Epidemic,purchase,1\r\n151603712,Dead Island Epidemic

In [0]:
from pyspark.sql.types import StructType, StructField, StringType, IntegerType, DoubleType

# This creates a custom schema for the Dataframe while converting it from CSV. It specifies the column names and datatype. 
stream_schema = StructType([
    StructField("user_id", IntegerType(), True),
    StructField("game_name", StringType(), True),
    StructField("action", StringType(), True),
    StructField("hours_played", DoubleType(), True)
])

# This creates a dataframe from the cssv file. We pass the schema as an option to the csv method. 
stream_data_DF = spark.read.csv(file_path, header = "true", schema = stream_schema, multiLine = "true")

# This prints dataframe's schema. 
stream_data_DF.printSchema()

# This prints the first 5 items in the dataframe. 
stream_data_DF.show(5)

root
 |-- user_id: integer (nullable = true)
 |-- game_name: string (nullable = true)
 |-- action: string (nullable = true)
 |-- hours_played: double (nullable = true)

+---------+--------------------+--------+------------+
|  user_id|           game_name|  action|hours_played|
+---------+--------------------+--------+------------+
|151603712|The Elder Scrolls...|    play|       273.0|
|151603712|           Fallout 4|purchase|         1.0|
|151603712|           Fallout 4|    play|        87.0|
|151603712|               Spore|purchase|         1.0|
|151603712|               Spore|    play|        14.9|
+---------+--------------------+--------+------------+
only showing top 5 rows



The cell below creates a temporary named _streamdata_. This view only exists in the current Spark session and it allows us to run SQL queries just like you would against a database. The method _createOrReplaceTempView_ will create a new view if a view with that name does not exist or replace the existing one, if one exists. 

In [0]:
#  Create temporary view.
stream_data_DF.createOrReplaceTempView ("streamdata")

**Data Exploration**

After saving the dataset into a view. I'm going to do some data exploration to answer some questions that I have. 

In [0]:
%sql

-- This is some data exploration just to gather some insights from the dataset. 

-- This query was trying to determine whether we have multiple plays for each user per game. From exploring the data, it does not seem to be the case. 

SELECT user_id, action, game_name, count(*) as frequency FROM `streamdata` group by user_id, action, game_name order BY user_id desc

user_id action game_name frequency 309903146 play Dota 2 1 309903146 purchase Dota 2 1 309824202 purchase Dota 2 1 309824202 play Dota 2 1 309812026 purchase Counter-Strike Nexon Zombies 1 309812026 purchase Robocraft 1 309626088 purchase Age of Empires II HD Edition 1 309626088 play Age of Empires II HD Edition 1 309554670 purchase Mitos.is The Game 1 309554670 play Mitos.is The Game 1 309434439 purchase Dota 2 1 309434439 play Dota 2 1 309404240 play Unturned 1 309404240 play Mitos.is The Game 1 309404240 play AdVenture Capitalist 1 309404240 play Team Fortress 2 1 309404240 purchase AdVenture Capitalist 1 309404240 play Transformice 1 309404240 purchase Unturned 1 309404240 purchase Team Fortress 2 1 309404240 purchase Mitos.is The Game 1 309404240 purchase Transformice 1 309375103 purchase East India Company Gold 1 309265377 play Brawlhalla 1 309265377 purchase Brawlhalla 1 309265377 play MicroVolts Surge 1 309265377 purchase MicroVolts Surge 1 309262440 purchase CrimeCraft GangWars 1 309262440 play Team Fortress 2 1 309262440 purchase A.V.A - Alliance of Valiant Arms 1 309262440 purchase Team Fortress 2 1 309255941 purchase Mitos.is The Game 1 309255941 play Mitos.is The Game 1 309228590 purchase Dota 2 1 309228590 play Dota 2 1 309216884 purchase Dota 2 1 309216884 play Dota 2 1 309213952 play Dota 2 1 309213952 purchase Dota 2 1 309188905 play Unturned 1 309188905 purchase Counter-Strike Nexon Zombies 1 309188905 play Counter-Strike Nexon Zombies 1 309188905 purchase Unturned 1 309181805 purchase Apotheon Arena 1 309181805 purchase Brawlhalla 1 309181805 play Brawlhalla 1 309167186 purchase Portal 2 1 309167186 play Portal 2 1 309138595 purchase Dota 2 1 309138595 play Dota 2 1 309107542 purchase Dota 2 1 309107542 play Dota 2 1 309058572 play Dota 2 1 309058572 purchase Dota 2 1 309052991 purchase Heroes & Generals 1 309052991 purchase Happy Wars 1 309052991 purchase Brawlhalla 1 309052991 play Heroes & Generals 1 309052991 play Brawlhalla 1 309038666 play Dota 2 1 309038666 purchase Dota 2 1 308997600 purchase Call of Duty Black Ops III 1 308997600 play Call of Duty Black Ops III 1 308971716 purchase Fishing Planet 1 308971716 play Fishing Planet 1 308970742 play Counter-Strike Nexon Zombies 1 308970742 purchase Counter-Strike Nexon Zombies 1 308954355 play Dota 2 1 308954355 purchase Dota 2 1 308940605 play Dota 2 1 308940605 purchase Dota 2 1 308925147 purchase Pool Nation FX 1 308925132 purchase Dota 2 1 308925132 play Dota 2 1 308894258 play Counter-Strike Global Offensive 1 308894258 purchase Counter-Strike Global Offensive 1 308880998 play Team Fortress 2 1 308880998 purchase Team Fortress 2 1 308851621 purchase Team Fortress 2 1 308851621 play Team Fortress 2 1 308851352 purchase War Thunder 1 308819212 purchase Dota 2 1 308819212 play Dota 2 1 308770654 purchase Dota 2 1 308770654 play Dota 2 1 308760273 purchase Team Fortress 2 1 308760273 play Toribash 1 308760273 purchase Toribash 1 308760273 play Team Fortress 2 1 308760273 play Unturned 1 308760273 purchase Unturned 1 308695132 purchase Champions Online 1 308695132 purchase La Tale 1 308695132 play Counter-Strike Nexon Zombies 1 308695132 purchase Brawlhalla 1 308695132 purchase Counter-Strike Nexon Zombies 1 308695132 play La Tale 1 308695132 play Champions Online 1 308695132 play Brawlhalla 1 308692673 purchase Dota 2 1 308692673 play Dota 2 1 308691324 purchase Team Fortress 2 1 308691324 play Team Fortress 2 1 308653033 play Unturned 1 308653033 purchase theHunter 1 308653033 purchase Unturned 1 308638385 purchase Dota 2 1 308638385 play Dota 2 1 308615060 purchase Dota 2 1 308615060 play Dota 2 1 308563852 purchase Dota 2 1 308563852 play Dota 2 1 308503685 purchase Counter-Strike Global Offensive 1 308503685 play Counter-Strike Global Offensive 1 308468736 play Magic Duels 1 308468736 purchase War Thunder 1 308468736 purchase Magic Duels 1 308468736 play War Thunder 1 308468736 purchase Metal War Online Retribution 1 308459721 purchase Dota 2 1 3084

In [0]:
%sql
-- From reviewing the data we can see that some users bought multiple games and played multiple games. Some users bought more than played. 

SELECT user_id, action, count(*) as frequency FROM `streamdata` group by user_id, action order BY user_id ASC;


user_id action frequency 5250 play 6 5250 purchase 21 76767 play 20 76767 purchase 36 86540 play 15 86540 purchase 82 103360 purchase 10 144736 purchase 8 144736 play 1 181212 play 2 181212 purchase 12 229911 purchase 27 229911 play 18 298950 purchase 259 298950 play 175 299153 purchase 14 381543 play 1 381543 purchase 10 547685 purchase 25 547685 play 5 554278 purchase 28 554278 play 9 561758 purchase 148 561758 play 80 577614 play 1 577614 purchase 8 604988 purchase 8 622362 purchase 10 622362 play 4 635733 purchase 8 635733 play 1 683019 purchase 13 683019 play 2 714122 purchase 10 714122 play 3 748719 purchase 30 748719 play 15 835015 purchase 8 861238 purchase 9 861238 play 3 871990 play 3 871990 purchase 12 937567 play 2 937567 purchase 17 948368 play 3 948368 purchase 14 975449 play 202 975449 purchase 378 976129 purchase 8 976129 play 1 983600 purchase 12 983600 play 1 994489 play 6 994489 purchase 23 1006880 purchase 8 1024319 play 1 1024319 purchase 8 1072465 purchase 15 1072465 play 6 1129452 purchase 22 1129452 play 13 1135775 purchase 8 1135775 play 1 1268792 purchase 8 1268792 play 1 1364546 play 2 1364546 purchase 9 1423371 purchase 9 1423371 play 1 1601069 purchase 8 1601773 purchase 10 1603625 purchase 8 1612666 play 17 1612666 purchase 28 1665511 purchase 8 1699101 play 1 1699101 purchase 8 1713646 play 1 1713646 purchase 12 1834453 purchase 12 1834453 play 2 1851828 purchase 10 1936551 purchase 152 1936551 play 86 1950243 play 44 1950243 purchase 77 1971801 purchase 10 2039434 play 3 2039434 purchase 16 2083767 play 32 2083767 purchase 61 2087859 purchase 14 2110581 purchase 35 2110581 play 28 2184507 purchase 12 2184507 play 3 2259650 play 111 2259650 purchase 203 2382003 purchase 8 2428602 purchase 15 2428602 play 2 2531540 play 7 2531540 purchase 29 2613043 purchase 8 2613043 play 1 2643609 purchase 49 2643609 play 29 2753525 play 57 2753525 purchase 118 3001740 purchase 10 3054990 purchase 8 3054990 play 1 3238976 play 1 3238976 purchase 8 3244702 purchase 12 3244702 play 3 3249166 play 1 3249166 purchase 8 3347312 purchase 8 3347312 play 1 3372923 purchase 10 3449240 purchase 98 3449240 play 57 3450426 play 5 3450426 purchase 8 3498717 play 1 3498717 purchase 12 3527485 play 15 3527485 purchase 23 3614782 purchase 14 3663009 play 1 3663009 purchase 12 3674653 play 1 3674653 purchase 8 3747293 play 1 3747293 purchase 12 3783783 purchase 27 3783783 play 19 3897969 purchase 8 3897969 play 1 3974133 purchase 8 3979930 play 17 3979930 purchase 27 4064412 play 4 4064412 purchase 11 4156158 purchase 8 4156158 play 1 4318904 purchase 8 4325465 play 1 4325465 purchase 8 4485779 play 1 4485779 purchase 8 4595423 play 9 4595423 purchase 27 4603800 purchase 10 4603800 play 1 4677023 purchase 8 4677023 play 1 4812175 purchase 8 4812175 play 2 4824107 play 14 4824107 purchase 34 4834220 purchase 33 4834220 play 16 4877411 purchase 12 4877411 play 5 4897767 play 1 4897767 purchase 8 4986667 purchase 8 4986667 play 1 5217749 purchase 12 5217749 play 1 5220782 purchase 16 5220782 play 4 5232588 purchase 8 5232588 play 3 5270060 purchase 18 5270060 play 5 5307960 purchase 8 5307960 play 1 5314150 purchase 7 5387470 purchase 72 5387470 play 35 5600822 play 1 5600822 purchase 12 5689496 play 1 5689496 purchase 12 5759284 purchase 8 5759284 play 1 5860071 purchase 15 5860071 play 7 5949488 purchase 17 5949488 play 5 5976642 play 5 5976642 purchase 13 5990132 purchase 53 5990132 play 38 6144819 purchase 33 6144819 play 14 6216773 purchase 3 6252885 purchase 14 6252885 play 4 6394150 purchase 3 6439568 purchase 11 6439568 play 6 6656519 play 1 6656519 purchase 3 6717871 purchase 122 6717871 play 49 6820462 play 3 6820462 purchase 9 6928806 play 20 6928806 purchase 34 6979578 purchase 3 6979578 play 3 7015471 play 17 7015471 purchase 39 7020135 purchase 14 7020135 play 3 7094039 purchase 3 7094039 play 3 7163917 play 7 7163917 purchase 20 7203603 play 17 7203603 purchase 33 7249363 purchase 11 7249363 play 6 7273540 play 2 727

In [0]:
%sql
-- This query finds users who have only done "purchase" actions and no "play" actions (or any other actions). 

SELECT user_id, count(*) FROM `streamdata` GROUP BY user_id HAVING COUNT(DISTINCT action) = 1 AND MAX(action) = 'purchase';

user_id count(1) 103360 10 299153 14 604988 8 835015 8 1006880 8 1601069 8 1601773 10 1603625 8 1665511 8 1851828 10 1971801 10 2087859 14 2382003 8 3001740 10 3372923 10 3614782 14 3974133 8 4318904 8 5314150 7 6216773 3 6394150 3 7507458 8 7617325 8 7987640 3 8415723 8 8817922 7 8978697 8 9439949 8 9548378 3 9811609 8 10144413 7 10262121 6 10267553 4 10810391 6 11080937 4 11200326 4 11408688 4 11504910 4 11613587 7 11650340 4 12034137 4 13669241 4 14095190 3 14256995 10 14416572 3 14421986 8 14433556 4 14706578 7 15084368 3 15432026 4 15503746 7 15824958 3 15841586 4 15902605 4 16261218 4 16285568 4 16717658 3 16821928 5 17135392 4 17531316 6 17947811 4 18607065 2 18611287 3 18675025 4 20266830 6 20498360 7 20593648 4 20724394 6 20781671 3 21261374 8 21551002 6 21805245 3 21822362 8 22277642 6 22503648 6 22883395 6 23046596 6 23078763 6 23219829 6 23432272 4 23609845 3 23780966 4 23918050 3 24258916 3 24445668 1 24555705 4 24583127 6 24583629 4 24817862 1 24872208 6 25031952 8 25272022 4 25349446 3 25634320 6 25710556 1 25822628 6 25827559 6 25831175 6 25864738 2 25889289 4 26218938 4 26491227 4 26593066 4 26601561 6 26779878 4 27060918 3 27116257 4 27275017 2 27371247 6 27500674 2 27578696 6 28165186 6 28851953 3 29078995 3 29122428 3 29405242 3 29603217 3 29736184 6 29926116 1 30007387 2 30010437 4 30041199 2 30142763 2 30283133 2 30323574 2 30574622 3 30710202 6 30734023 2 30985722 2 31063925 2 31069041 2 31124692 2 31188792 2 31319953 1 31598106 2 31616745 4 31757271 4 32021037 6 32617936 2 33023846 2 33033120 1 33228985 13 33250362 2 33291661 5 33434940 1 33479807 1 33577800 2 33583543 2 33658023 2 33705095 2 33934276 1 34150817 1 34161935 5 34618463 3 34679511 1 34863766 4 35116894 2 35192186 8 35418544 1 35432082 2 35935953 3 36083584 4 36157772 2 36188511 1 36257313 2 36495125 6 36933405 1 36963214 10 37068073 2 37226272 2 37252377 1 37419728 6 37420720 2 37522295 2 37643786 4 37659112 2 38132168 2 38853323 2 38937590 6 38978172 2 39010350 2 39654762 2 39663272 2 39671216 2 39795967 3 40045419 4 41407280 6 41917762 4 42464885 1 42493197 1 42642155 2 42799637 1 43093291 1 43518355 3 43551909 1 43583319 1 43989530 5 44043970 4 44221885 5 45274432 1 46800342 1 46856734 1 47596241 2 47636024 2 47748424 1 48688347 4 48772264 5 48951291 1 49469819 1 50810886 1 50825641 1 51044834 1 51098091 1 51237520 3 51268450 4 51429054 2 51626428 2 51938138 1 52022614 1 52438281 1 52559629 1 53678595 3 54092998 1 54111916 1 54531801 1 54553556 5 54680190 3 54704882 1 55363009 1 55525449 1 55691331 1 55948496 2 56830362 1 57333945 13 57670085 1 58393019 2 59025651 1 59219245 3 59264152 2 60209945 2 60236480 8 60701208 3 61044093 1 61068356 1 61098124 1 61635781 1 61642722 2 61707834 1 61831445 3 61935579 2 62848935 1 63294797 3 63595926 2 63962362 1 64158475 1 64689644 1 64849879 1 64936592 1 65438630 1 65758675 1 66006698 3 66215101 2 68081395 1 69371602 1 69729762 1 69796945 1 69880609 1 70373768 1 70395325 1 70470505 1 71083492 1 71302392 1 71331890 2 71486921 1 72471210 2 73435656 1 73507733 1 73767750 1 74221955 1 74738483 1 74874862 2 75419274 1 75515543 1 76095365 4 76190673 2 76684659 1 76768611 1 77163444 1 79124111 1 79180628 1 79216711 4 79219608 1 79455558 1 80173910 2 80419227 2 80984802 1 81079291 2 81711607 1 82807945 1 82895724 3 83028567 2 83310356 1 84024556 2 84948626 1 85625611 1 85736530 1 86828660 1 87886634 3 87947085 1 88587483 1 88626156 2 88715858 1 88770649 2 89245804 2 89360306 1 89539775 2 89988424 1 90735121 2 91040629 1 93454114 1 93745851 2 93774169 1 94156206 1 94429644 4 94751685 1 94778390 1 94842963 2 94865453 2 94931090 2 94961328 1 94965694 2 94982344 2 95103912 1 95316727 1 95445569 1 95854541 1 95924900 5 97234778 1 97475059 3 97564287 1 97626507 1 97913360 1 98194674 1 98789695 1 99162218 1 99202472 1 99372794 4 100642975 5 101040836 1 101399037 1 101865671 3 102257546 1 102494404 1 104265574 2 105289933 3 105885524 1 106147639 2 106802395 1 108435168 3 108726847 7 108872482 1 110473936 1 1104805

Databricks visualization. Run in Databricks to view.

In [0]:
%sql
-- Check if any user played for 0 hours. No user played 0 hours of games. 

SELECT user_id from `streamdata` where action = 'play' and hours_played = 0;

user_id

In [0]:
%sql

-- Check the play action had any values less than 1. 

SELECT game_name, user_id, hours_played from `streamdata` where action = 'play' and hours_played <= 1;


game_name user_id hours_played Fallout 3 - Game of the Year Edition 151603712 0.8 SEGA Genesis & Mega Drive Classics 151603712 0.8 Grand Theft Auto IV 151603712 0.6 Realm of the Mad God 151603712 0.5 Marvel Heroes 2015 151603712 0.5 Eldevin 151603712 0.5 Dota 2 151603712 0.5 BioShock 151603712 0.5 Robocraft 151603712 0.4 Garry's Mod 151603712 0.1 Jazzpunk 151603712 0.1 Orcs Must Die! 59945701 0.7 THE KING OF FIGHTERS XIII STEAM EDITION 59945701 0.6 GUILTY GEAR XX ACCENT CORE PLUS R 59945701 0.5 Skullgirls 59945701 0.4 Assassin's Creed II 59945701 0.3 Company of Heroes Opposing Fronts 59945701 0.1 Team Fortress 2 59945701 0.1 LUFTRAUSERS 53875128 1.0 Arma 2 53875128 1.0 No Time To Explain Remastered 53875128 0.9 FEZ 53875128 0.9 Delver 53875128 0.9 The Legend of Heroes Trails in the Sky 53875128 0.9 Evoland 53875128 0.9 Bleed 53875128 0.8 Borderlands 2 53875128 0.8 Race The Sun 53875128 0.8 Shadowgrounds 53875128 0.8 They Bleed Pixels 53875128 0.8 BioShock 53875128 0.8 Trine 53875128 0.8 Sir, You Are Being Hunted 53875128 0.8 Next Car Game Sneak Peek 2.0 53875128 0.7 Symphony 53875128 0.7 DLC Quest 53875128 0.7 Far Cry 2 53875128 0.7 The Stanley Parable 53875128 0.6 Freedom Planet 53875128 0.6 KHOLAT 53875128 0.6 Osmos 53875128 0.6 Secrets of Rtikon 53875128 0.6 Oil Rush 53875128 0.6 Unepic 53875128 0.6 FINAL FANTASY VII 53875128 0.6 The Legend of Korra 53875128 0.5 404Sight 53875128 0.5 Dark Souls Prepare to Die Edition 53875128 0.5 Gravity Ghost 53875128 0.5 Psychonauts 53875128 0.5 Rock of Ages 53875128 0.5 Spore 53875128 0.5 Half-Life 2 Lost Coast 53875128 0.5 Galcon Legends 53875128 0.5 Air Brawl 53875128 0.5 Cat Goes Fishing 53875128 0.5 One Finger Death Punch 53875128 0.5 Mind Path to Thalamus Enhanced Edition 53875128 0.4 INK 53875128 0.4 Intrusion 2 53875128 0.4 Amnesia The Dark Descent 53875128 0.4 Fieldrunners 53875128 0.4 Out There Somewhere 53875128 0.4 KAMI 53875128 0.4 Lone Survivor The Director's Cut 53875128 0.4 NightSky 53875128 0.4 Frozen Synapse 53875128 0.4 Hammerfight 53875128 0.4 Spintires 53875128 0.4 Ziggurat 53875128 0.4 AaaaaAAaaaAAAaaAAAAaAAAAA!!! for the Awesome 53875128 0.4 Dead Island 53875128 0.3 Superbrothers Sword & Sworcery EP 53875128 0.3 GRID 2 53875128 0.3 Sonic & All-Stars Racing Transformed 53875128 0.3 Call of Juarez Gunslinger 53875128 0.3 Crysis 2 Maximum Edition 53875128 0.3 Strike Vector 53875128 0.3 Prison Architect 53875128 0.3 Lego Harry Potter 53875128 0.3 Outlast 53875128 0.3 Super Hexagon 53875128 0.2 WRC 4 FIA WORLD RALLY CHAMPIONSHIP 53875128 0.2 Valkyria Chronicles 53875128 0.2 Shatter 53875128 0.2 Proteus 53875128 0.2 Jamestown 53875128 0.2 Spelunky 53875128 0.2 Astebreed 53875128 0.2 STAR WARS Knights of the Old Republic II The Sith Lords 53875128 0.2 Phantom Breaker Battle Grounds 53875128 0.2 Tom Clancy's Splinter Cell Chaos Theory 53875128 0.2 The Witcher Enhanced Edition 53875128 0.2 Risk of Rain 53875128 0.2 Survarium 53875128 0.2 Afterlife Empire 53875128 0.2 BattleBlock Theater 53875128 0.2 Need for Speed Hot Pursuit 53875128 0.2 BIT.TRIP RUNNER 53875128 0.1 Coin Crypt 53875128 0.1 Skullgirls 53875128 0.1 The Crew 53875128 0.1 Metro Last Light Redux 53875128 0.1 Crimzon Clover WORLD IGNITION 53875128 0.1 Sonic Generations 53875128 0.1 Ethan Meteor Hunter 53875128 0.1 Reus 53875128 0.1 Dota 2 197278511 0.5 Alien Swarm 76933274 1.0 TERA 218323237 0.9 Everlasting Summer 126340495 0.6 Dead Island Epidemic 126340495 0.6 War Thunder 126340495 0.4 DCS World 126340495 0.3 Tactical Intervention 194895541 0.4 Unturned 308653033 0.6 Mark of the Ninja 97298878 0.9 Burnout Paradise The Ultimate Box 97298878 0.6 Mirror's Edge 97298878 0.5 Crysis 2 Maximum Edition 97298878 0.5 Painkiller Overdose 97298878 0.4 Cogs 97298878 0.2 Crayon Physics Deluxe 97298878 0.2 Osmos 97298878 0.1 Hotline Miami 2 Wrong Number 92107940 0.8 Amnesia A Machine for Pigs 92107940 0.5 Dota 2 251431515 0.9 Counter-Strike 30695285 0.2 SMITE 48845802 0.9 Ricochet 48845802 0.3 Kane & Lynch 2 Dog Days 48845802


#### Creating Numeric Unique ID for all Distinct Games 

Because ALS requires numeric IDs to be able to train the algorithm. We need to generate an ID for the games. ALS converts your user-item interaction data into a sparse matrix where:
- Rows = Users
- Columns = Items (Games)


Spark internally uses integer-based indexing to represent matrix rows and columns efficiently. Other data types take up more memory and slow down matrix math.

This was done by first selecting all the unique games and generating an ID for them using the _**monotonically_increasing_id**_() method and saving them in a dataframe. The next step is to join that dataframe back to the initial dataframe using the **_game_name_**. 


In [0]:
# Generate Game ID for all distinct games 

from pyspark.sql.functions import monotonically_increasing_id

# Get distinct game names and assign each a unique ID
game_name_with_game_id_DF = stream_data_DF.select("game_name").distinct() \
    .withColumn("game_id", monotonically_increasing_id())

# Join the new game IDs back into the main DataFrame
stream_data_with_game_id_DF = stream_data_DF.join(game_name_with_game_id_DF, on="game_name", how="inner")


In [0]:
# This cell displays the dataframe with the new game_id
stream_data_with_game_id_DF.show(10)

+--------------------+---------+--------+------------+-------+
|           game_name|  user_id|  action|hours_played|game_id|
+--------------------+---------+--------+------------+-------+
|The Elder Scrolls...|151603712|    play|       273.0|   3036|
|           Fallout 4|151603712|purchase|         1.0|    478|
|           Fallout 4|151603712|    play|        87.0|    478|
|               Spore|151603712|purchase|         1.0|   4524|
|               Spore|151603712|    play|        14.9|   4524|
|   Fallout New Vegas|151603712|purchase|         1.0|   4470|
|   Fallout New Vegas|151603712|    play|        12.1|   4470|
|       Left 4 Dead 2|151603712|purchase|         1.0|     86|
|       Left 4 Dead 2|151603712|    play|         8.9|     86|
|            HuniePop|151603712|purchase|         1.0|   3893|
+--------------------+---------+--------+------------+-------+
only showing top 10 rows



### Calculating the Interaction Strength and Confidence

In this dataset, Purchase and Play actions are implicit feedback, with a value of 1 for Purchase. The feedback represent the strength of the user's interaction rather than the user's preference which is the case in explicit feedback like ratings. For implicit feedback, we need to create a representation of our implicit feedback values. This is used to calculate the preference or interaction strength. The preference can be a binary representation or a set of values ranging from 0 to 1. I have gone with values from 0 to 1. 

![Confidence and Preference](/files/tables/preference_confidence.png)

##### Interaction Strength Rationale
- Played ≥ 10 hrs	1.0	Highly engaged
- Played 5–10 hrs	0.8	Medium engagement
- Played 1–5 hrs	0.6	Weak engagement
- Played < 1 hr	0.3	Low interest (possibly abandoned)
- No interaction	0.1	No data – treated as unknown
- Purchase: if a game was purchased but wasn't played: 0.2 

##### Confidence

Instead of representing an explicit rating,  we can represent a “confidence” in terms of how strong the interaction was. Items with a larger number of hours played can carry more weight in our ratings matrix. This is calculated automatically by ALS as it accepts an option of alpha. 


##### References
- https://stackoverflow.com/questions/25122798/how-to-manage-multiple-positive-implicit-feedbacks
- http://yifanhu.net/PUB/cf.pdf
- https://medium.com/radon-dev/als-implicit-collaborative-filtering-5ed653ba39fe


In [0]:
from pyspark.sql.functions import when, col, max

# Assign interaction strength based on engagement:
# - Playing is treated as a stronger signal than purchasing,
#   since users must purchase before they can play.
# - Higher playtime = stronger interest.


# Create flags for each user-game interaction
interaction_flags = stream_data_with_game_id_DF.groupBy("user_id", "game_id").agg(
    max(when(col("action") == "purchase", 1).otherwise(0)).alias("purchased"),
    max(when(col("action") == "play", 1).otherwise(0)).alias("played"),
    max(when(col("action") == "play", col("hours_played"))).alias("max_hours_played")
)

interaction_flags = interaction_flags.fillna({"max_hours_played": 0.0})

stream_data_with_interaction_strength_DF = interaction_flags.withColumn(
    "interaction_strength",
    
    # High engagement
    when((col("played") == 1) & (col("max_hours_played") >= 10), 1.0)
    .when((col("played") == 1) & (col("max_hours_played") >= 5), 0.8)
    .when((col("played") == 1) & (col("max_hours_played") >= 1), 0.6)
    .when((col("played") == 1) & (col("max_hours_played") < 1), 0.3)
    
    # Only purchased, no play
    .when((col("purchased") == 1) & (col("played") == 0), 0.2)
    
    # No meaningful interaction
    .otherwise(0.1)
)

# Clean the data
training_clean = stream_data_with_interaction_strength_DF.select(
    col("user_id").cast("int"),
    col("game_id").cast("int"),
    col("interaction_strength").cast("float")
).dropna()


training_clean.show(10)



+---------+-------+--------------------+
|  user_id|game_id|interaction_strength|
+---------+-------+--------------------+
|151603712|     86|                 0.8|
| 59945701|   1457|                 0.2|
| 53875128|   5107|                 0.2|
| 97298878|   4709|                 0.2|
| 11373749|   2354|                 0.6|
| 11373749|   1179|                 0.2|
| 11373749|   3322|                 0.2|
| 11373749|   1921|                 0.2|
|154868247|    292|                 0.2|
|185040259|   4084|                 0.6|
+---------+-------+--------------------+
only showing top 10 rows



The cell below, the first line splits the preprocessed data into training and tests set in an 80-20% ratio. 

The next step is to configure the Alternating Least Square (ALS) algorithm which is the core step for building recommendation system. 

The ALS model is configured using different options namely: 

- userCol
- itemCol
- ratingCol
- implicitPrefs
- seed
- coldStartStrategy



In [0]:
from pyspark.ml.recommendation import ALS

# Split the cleaned dataset into training and test sets (80% training, 20% test)
(training, test) = training_clean.randomSplit([0.8, 0.2], seed=100)

# Configure the ALS (Alternating Least Squares) recommender model
als = ALS(
    userCol="user_id",    # Column representing the user ID
    itemCol="game_id",    # Column representing the item (game) ID
    ratingCol="interaction_strength",  # Column representing implicit feedback signal
    implicitPrefs=True, # Treat the input as implicit feedback (not explicit ratings
    seed=100, # Set seed for reproducibility
    coldStartStrategy="drop" # Treat the input as implicit feedback (not explicit ratings
)

# Train the ALS model using the training datas
model = als.fit(training)



2025/04/24 10:48:29 INFO mlflow.utils.autologging_utils: Created MLflow autologging run with ID 'a64cb1daaee04add8203aabbbf3e1f30', which will track hyperparameters, performance metrics, model artifacts, and lineage information for the current pyspark.ml workflow
2025/04/24 10:49:47 WARNING mlflow.pyspark.ml: Model ALS_b891f32da9f7 will not be autologged because it is not allowlisted or or because one or more of its nested models are not allowlisted. Call mlflow.spark.log_model() to explicitly log the model, or specify a custom allowlist via the spark.mlflow.pysparkml.autolog.logModelAllowlistFile Spark conf (see mlflow.pyspark.ml.autolog docs for more info).


The code in the cell below trains an ALS model using implicit feedback data. It also performs hyperparameter tuning with TrainValidationSplit and logs the best result to MLflow. 

The parameters defined are: 
- rank: number of latent features (5, 10)
- regParam: regularization (0.01, 0.005)
- alpha: confidence weight for implicit feedback (20, 40)
- maxIter: number of training iterations (fixed at 10)


The model was evaluated using RMSE metric. 

In [0]:
from pyspark.ml.recommendation import ALS
from pyspark.ml.tuning import ParamGridBuilder, CrossValidator, TrainValidationSplit
from pyspark.ml.evaluation import RegressionEvaluator

# Create parameter grid
paramGrid = ParamGridBuilder() \
    .addGrid(als.rank, [5, 10]) \
    .addGrid(als.regParam, [0.01, 0.005]) \
    .addGrid(als.alpha, [20, 40]) \
    .addGrid(als.maxIter, [10]) \
    .build()

# Define evaluator
evaluator = RegressionEvaluator(metricName="rmse", labelCol="interaction_strength", predictionCol="prediction")


# Create TrainValidationSplit (for hyperparameter tuning)
tvs = TrainValidationSplit() \
    .setSeed(20) \
    .setTrainRatio(0.80) \
    .setEstimatorParamMaps(paramGrid) \
    .setEstimator(als) \
    .setEvaluator(evaluator) \
    .setParallelism(8)


# End any existing run
mlflow.end_run()

with mlflow.start_run(run_name="ALS_with_TrainValidationSplit"):

    # Fit model
    tvs_model = tvs.fit(training)
    best_model = tvs_model.bestModel

    # ALS only makes predictions for user-item pairs it has seen during training. If your test set contains:
    best_model.setColdStartStrategy("drop")

    
    predictions = best_model.transform(test)
    rmse = evaluator.evaluate(predictions)

    print("RMSE:", rmse)


     # Log only the best params
    mlflow.log_param("best_rank", best_model.rank)
    mlflow.log_param("best_regParam", best_model._java_obj.parent().getRegParam())
    mlflow.log_param("best_alpha", best_model._java_obj.parent().getAlpha())
    mlflow.log_param("best_maxIter", best_model._java_obj.parent().getMaxIter())

    mlflow.log_metric("best_rmse", rmse)
    mlflow.spark.log_model(best_model, "best_als_model")


    # Print best params
    print("Best rank:", best_model.rank)
    print("Best regParam:", best_model._java_obj.parent().getRegParam())
    print("Best maxIter:", best_model._java_obj.parent().getMaxIter())

2025/04/24 11:06:29 WARNING mlflow.pyspark.ml: Model TrainValidationSplitModel_1c3bf239f707 will not be autologged because it is not allowlisted or or because one or more of its nested models are not allowlisted. Call mlflow.spark.log_model() to explicitly log the model, or specify a custom allowlist via the spark.mlflow.pysparkml.autolog.logModelAllowlistFile Spark conf (see mlflow.pyspark.ml.autolog docs for more info).


RMSE: 0.42952838472305255


2025/04/24 11:06:52 INFO mlflow.spark: Inferring pip requirements by reloading the logged model from the databricks artifact repository, which can be time-consuming. To speed up, explicitly specify the conda_env or pip_requirements when calling log_model().
/databricks/python/lib/python3.9/site-packages/_distutils_hack/__init__.py:30: UserWarning: Setuptools is replacing distutils.
  warnings.warn("Setuptools is replacing distutils.")


Best rank: 5
Best regParam: 0.01
Best maxIter: 10


In [0]:
# This uses the best model to generate 10 recommendations (games) for all users in the dataset
userRecs = best_model.recommendForAllUsers(10)

This code in the cell below flattens the  output from recommendForAllUsers() into a flat form that's easy to read and understand. And proceed to visualize all 10 recommended games for a particular user. 

In [0]:
from pyspark.sql.functions import explode

exploded_df = userRecs.withColumn("recommendation", explode("recommendations")) \
    .select("user_id", "recommendation.game_id", "recommendation.rating")

# Step 2: Ensure games_df has only unique game_id → game_name pairs
# distinct_games_df = stream_data_with_interaction_strength_DF.select("game_id", "game_name").dropDuplicates(["game_id"])

distinct_games_df = stream_data_with_interaction_strength_DF.join(stream_data_with_game_id_DF, on = "game_id", how="inner").dropDuplicates(["game_id"]).select("game_id", "game_name")

# Step 3: Join exploded recommendations with games
user_recs_with_names = exploded_df \
    .join(distinct_games_df, on="game_id", how="inner")

# This filters out all recommended game for the particular user. 
target_user_id = 76767
user_final_recommendations = user_recs_with_names \
    .filter(user_recs_with_names.user_id == target_user_id)

user_final_recommendations.select("game_name", "rating", "game_id").orderBy("rating", ascending=False).show(10, truncate=False)

+-----------------------------------+---------+-------+
|game_name                          |rating   |game_id|
+-----------------------------------+---------+-------+
|Anodyne                            |1.1766244|4      |
|SanctuaryRPG Black Edition         |1.1104939|8      |
|Meltdown                           |1.0941837|7      |
|RIFT                               |1.067694 |3      |
|METAL GEAR SOLID V THE PHANTOM PAIN|1.0287501|1      |
|Divinity Original Sin              |1.0163019|6      |
|Legend of Grimrock                 |0.9976536|5      |
|Dota 2                             |0.9783784|0      |
|LEGO Batman The Videogame          |0.9617592|2      |
|Lunar Flight                       |0.9210408|10     |
+-----------------------------------+---------+-------+



This code in the cell below evaluates the ranking performance of a recommendation model using Precision@10, Mean Average Precision (MAP), and Normalized Discounted Cumulative Gain (NDCG@10). These are other evaluation metrics for implicit feedback. 

- Precision@10: The percentage of recommended items in the top 10 that are actually relevant.

- MAP: MAP considers how many relevant items you recommended, and how early in the list they appear — then averages that over all users.

- NDCG@10: It gives higher weight to correct items at the top of the list (e.g., slot #1 is worth more than slot #10).



In [0]:
from pyspark.sql.functions import collect_list, col, expr
from pyspark.mllib.evaluation import RankingMetrics

# Step 1: Group test data to get the actual items (games interacted with) per user
actual_items = test.groupBy("user_id") \
    .agg(collect_list("game_id").alias("true_items"))

# Step 2: Extract predicted game_ids from nested recommendations column
# recommendations is a list of structs -> extract game_id from each struct
predicted_items = userRecs.select(
    col("user_id"),
    expr("transform(recommendations, x -> x.game_id)").alias("predicted_items")
)

# Step 3: Join predicted and actual items on user_id and convert to RDD
predictionAndLabels = predicted_items.join(actual_items, "user_id") \
    .rdd.map(lambda row: (row.predicted_items, row.true_items))

# Step 4: Evaluate ranking metrics
rankingMetrics = RankingMetrics(predictionAndLabels)

# Step 5: Print evaluation scores
print("Precision@10 =", rankingMetrics.precisionAt(10))
print("Mean Average Precision =", rankingMetrics.meanAveragePrecision)
print("NDCG@10 =", rankingMetrics.ndcgAt(10))


/databricks/spark/python/pyspark/sql/context.py:165: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


Precision@10 = 0.01661255411255411
Mean Average Precision = 0.1122851950161524
NDCG@10 = 0.11931490836583936


#### Conclusion

The recommender system uses implicit user feedback to generate game recommendations using the ALS (Alternating Least Squares) algorithm. By generating  interaction_strength scores based on user behavior (e.g., playtime and purchases). 

After optimizing hyperparameters and refining interaction weights, the model achieved a significantly improved RMSE of 0.429, indicating strong accuracy in estimating user preferences. This marks a notable enhancement from earlier iterations and suggests the system has learned  user-game patterns.

However, while the model performs well numerically, ranking metrics such as Precision@10 (1.66%), MAP (0.11), and NDCG@10 (0.12) suggest that the recommendations could be further optimized to show more relevant items at the top of each user’s list. This indicates room for improvement.

Overall, the system provides some accurate recommendations, and there are some improvements that can be done to improve the other metrics. 